<div class="alert alert-block alert-info">
<span style="color: rgb(0,53,91);">
<center><img src="https://www.redage.org/sites/default/files/styles/large/public/img-logo-institucion/logo_iteso.jpg?itok=IzloBJS1" style="width:500px;height:142px;" title="Logo ITESO"></center>

<font face = "Times New Roman" size = "6"><b><center>Programacion para Mineria de Datos</center></b></font>
<font face = "Times New Roman" size = "5"><b><center>Preprocessing Production</center></b></font>

<b><font face = "Times New Roman" size = "5"><center>Final Proyect</center></font>
<div align="right"><font face = "Times New Roman" size = "2">nombres: Angel Aceves Manzo</font></div>
<div align="right"><font face = "Times New Roman" size = "2"> Jorge Arturo Ponce Martin</font></div>
<div align="right"><font face = "Times New Roman" size = "2"> Jesus Vargas Pacheco</font></div>
</span></div>

In [8]:

# Deben cargarse los archivos
# - preprocessor_cat.joblib
# - pca_pipe_num.joblib
# - pca_metadata.json
# - T_train_final_objetivo.csv
# - csv de tus nuevos datos
# Devolverá T_new_final.csv: el csv de PCA aplicado a los nuevos datos

# === importar librerias
import joblib
import json
import pandas as pd
#####################################################
preprocessor_cat = joblib.load("../preprocessing/preprocessor_cat.joblib")
pca_pipe = joblib.load("../preprocessing/pca_pipe_num.joblib")
with open("../preprocessing/pca_metadata.json", "r") as f:
#####################################################
    meta = json.load(f)

cols_num = meta["cols_num"]
cols_cat = meta["cols_cat"]
pc_cols  = meta["pc_cols"]
cat_out_cols = meta["cat_out_cols"]

# PCA DE ENTRENAMIENTO CON OBJETIVO
#####################################################
entrenamiento = pd.read_csv("../preprocessing/T_train_final_objetivo.csv")   ### todas las pca, categoricas y objetivo
print(entrenamiento)
#####################################################
entrenamiento_pca_objetivo = entrenamiento[pc_cols]



           PC1       PC2       PC3       PC4       PC5       PC6       PC7  \
0     0.471948 -0.579149  1.521629 -0.186432 -0.062978 -0.693230  0.025374   
1     2.509848  1.348587  3.889877 -1.284385  0.596133  2.553178 -1.509168   
2    -0.197581 -0.279411  1.457258 -0.376840  0.553272 -0.451123  0.479281   
3    -0.523115 -0.736739 -0.567720  0.364835  0.230557 -1.179599 -0.685428   
4     7.544555 -0.080174 -0.035884  0.019877 -0.401771  2.308790 -0.358973   
...        ...       ...       ...       ...       ...       ...       ...   
3745 -0.601659  0.117408 -0.274338  0.434337 -0.450983  0.401936  0.455584   
3746  6.439196 -0.035518  0.864560 -0.043236  0.143468  0.589822  1.053328   
3747 -0.450526  0.054279 -0.910250 -0.888399 -0.802484  0.839281 -0.671015   
3748 -0.389366 -0.794953 -0.137395  0.171760  0.820119 -0.216798 -0.014609   
3749 -0.228763 -0.882523 -0.795382  0.006074  0.421853 -1.172396  0.119390   

           PC8  Gender___female  Gender___male  ...  \
0     0.

In [9]:

# NUEVOS DATOS
#####################################################
new_df = pd.read_csv("../../data_Proyecto/ecommerce_customer_behavior_dataset_desconocido.csv")

#####################################################
X_new_num = new_df[cols_num]
X_new_cat = new_df[cols_cat]

# Categóricas (mismo encoder, sin re-ajustar)
X_new_cat_proc = preprocessor_cat.transform(X_new_cat)
df_new_cat_encode = pd.DataFrame(X_new_cat_proc, columns=cat_out_cols, index=new_df.index)

# Numéricas → (preproc_num + StdScaler + PCA) con el pipeline guardado
T_new = pca_pipe.transform(X_new_num)
T_new_df = pd.DataFrame(T_new, columns=pc_cols, index=new_df.index)

# Final
T_new_final = pd.concat([T_new_df, df_new_cat_encode], axis=1)
T_new_final.to_csv("T_new_final.csv",index=False)

In [10]:
import plotly.express as px
import plotly.graph_objects as go

# --- 1) figura base: train coloreado por objetivo 
y_train = entrenamiento["objetivo"]
df_plot2 = entrenamiento_pca_objetivo.iloc[:, :2].copy()
df_plot2["objetivo"] = y_train.loc[entrenamiento_pca_objetivo.index].astype(str)

fig = px.scatter(
    df_plot2, x="PC1", y="PC2", color="objetivo",
    opacity=0.85, title="PC1 vs PC2 — Train (objetivo) + Nuevos",
    height=550
)
fig.update_traces(marker=dict(size=6))

# --- 2) overlay: nuevos (un solo trazo, símbolo distinto) ---
new2 = T_new_df.loc[:, ["PC1", "PC2"]].copy()
fig.add_trace(
    go.Scatter(
        x=new2["PC1"], y=new2["PC2"],
        mode="markers",
        name="nuevos",
        marker=dict(size=9, line=dict(width=1)),
        opacity=0.95,
        showlegend=True
    )
)

fig.update_layout(xaxis_title="PC1", yaxis_title="PC2")
fig.show()


In [11]:
T_new_final

PC1       PC2       PC3       PC4       PC5       PC6       PC7  \
0    -0.692877  1.032777 -0.811072  0.176299 -0.444821  0.352530  1.414467   
1     1.054198 -0.483213 -1.270369 -0.444324 -0.792460  0.956465 -0.695790   
2    -0.262991 -0.122821 -0.112807 -0.485023  1.208143  0.173519  0.999320   
3     0.105105 -0.331374  1.299969 -0.746034  1.375707  0.587868 -0.217713   
4    -0.437961 -0.307147 -0.267445 -0.051726  0.160202 -0.729264 -0.096727   
..         ...       ...       ...       ...       ...       ...       ...   
498  12.176259  0.233507 -1.247540 -1.021271  0.844178 -0.188070  0.563561   
499  20.631091  0.319757 -0.826976  0.256304  0.824847 -0.114197 -0.731841   
500  -0.322684  0.632491 -1.546464 -0.800185 -0.674125  1.104845  0.182613   
501  -0.069280 -0.765273  0.192590  0.373684  1.234150 -1.144064  0.266724   
502  -0.652604  1.059524  0.124659 -0.150293  0.232566  0.900951  0.981342   

          PC8  Gender___female  Gender___male  ...  \
0    0.314815              0.0            0.0  ...   
1    0.737608              0.0            0.0  ...   
2   -0.099657              0.0            0.0  ...   
3    0.718896              0.0            0.0  ...   
4    0.052498              0.0            0.0  ...   
..        ...              ...            ...  ...   
498  9.003925              0.0            0.0  ...   
499  9.901425              0.0            0.0  ...   
500 -0.208569              0.0            0.0  ...   
501  0.553110              0.0            0.0  ...   
502  0.268643              0.0            0.0  ...   

     Payment_Method___bank transfer  Payment_Method___cash on delivery  \
0                               0.0                                0.0   
1                               0.0                                0.0   
2                               0.0                                0.0   
3                               0.0                                0.0   
4                               0.0                                0.0   
..                              ...                                ...   
498                             0.0                                0.0   
499                             0.0                                0.0   
500                             0.0                                0.0   
501                             0.0                                0.0   
502                             0.0                                0.0   

     Payment_Method___credit card  Payment_Method___debit card  \
0                             0.0                          0.0   
1                             0.0                          0.0   
2                             0.0                          0.0   
3                             0.0                          0.0   
4                             0.0                          0.0   
..                            ...                          ...   
498                           0.0                          0.0   
499                           0.0                          0.0   
500                           0.0                          0.0   
501                           0.0                          0.0   
502                           0.0                          0.0   

     Payment_Method___digital wallet  Device_Type___desktop  \
0                                0.0                    0.0   
1                                0.0                    0.0   
2                                0.0                    0.0   
3                                0.0                    0.0   
4                                0.0                    0.0   
..                               ...                    ...   
498                              0.0                    0.0   
499                              0.0                    0.0   
500                              0.0                    0.0   
501                              0.0                    0.0   
502                              0.0              

In [12]:
new_df

Order_ID Customer_ID        Date  Age  Gender      City  \
0     ORD_000001-1  CUST_00001  29/05/2023   40    Male    Ankara   
1     ORD_000001-2  CUST_00001  12/10/2023   40    Male    Ankara   
2     ORD_000001-3  CUST_00001  05/12/2023   40    Male    Ankara   
3     ORD_000002-1  CUST_00002  11/05/2023   33    Male  Istanbul   
4     ORD_000002-2  CUST_00002  16/06/2023   33    Male  Istanbul   
..             ...         ...         ...  ...     ...       ...   
498   ORD_000154-6  CUST_00154  15/10/2023   37  Female     Izmir   
499   ORD_000154-7  CUST_00154  12/12/2023   37  Female     Izmir   
500   ORD_000154-8  CUST_00154  06/02/2024   37  Female     Izmir   
501   ORD_000154-9  CUST_00154  14/02/2024   37  Female     Izmir   
502  ORD_000154-10  CUST_00154  24/02/2024   37  Female     Izmir   

    Product_Category  Unit_Price  Quantity  Discount_Amount  Total_Amount  \
0              Books       29.18         1             0.00         29.18   
1      Home & Garden      644.40         1           138.05        506.35   
2             Sports      332.82         5             0.00       1664.10   
3               Food       69.30         5            71.05        275.45   
4             Beauty      178.15         3             0.00        534.45   
..               ...         ...       ...              ...           ...   
498      Electronics     1981.17         5          1289.04       8616.81   
499      Electronics     5677.63         4          1848.10      20862.42   
500          Fashion      484.53         1             0.00        484.53   
501             Food       56.34         5            47.84        233.86   
502             Food       43.26         2             0.00         86.52   

     Payment_Method Device_Type  Session_Duration_Minutes  Pages_Viewed  \
0    Digital Wallet      Mobile                        14             9   
1       Credit Card     Desktop                        14             8   
2       Credit Card      Mobile                        15            10   
3    Digital Wallet     Desktop                        16            13   
4       Credit Card      Mobile                        14             7   
..              ...         ...                       ...           ...   
498     Credit Card     Desktop                         6             8   
499   Bank Transfer      Mobile                        13             8   
500   Bank Transfer      Mobile                        15             9   
501  Digital Wallet      Mobile                        17             7   
502      Debit Card      Mobile                        17            12   

     Is_Returning_Customer  Delivery_Time_Days  Customer_Rating  
0                     True                  13                4  
1                     True                   6                2  
2                     True                   9                4  
3                     True                   4                4  
4                     True                   6                4  
..                     ...                 ...              ...  
498                   True                  10                4  
499                   True                   5                5  
500                   True                  11                2  
501                   True                   5                5  
502                   True                  11                4  

[503 rows x 18 columns]

In [13]:
df_merged = pd.merge(new_df,T_new_final,left_index=True,right_index=True)
df_merged

Order_ID Customer_ID        Date  Age  Gender      City  \
0     ORD_000001-1  CUST_00001  29/05/2023   40    Male    Ankara   
1     ORD_000001-2  CUST_00001  12/10/2023   40    Male    Ankara   
2     ORD_000001-3  CUST_00001  05/12/2023   40    Male    Ankara   
3     ORD_000002-1  CUST_00002  11/05/2023   33    Male  Istanbul   
4     ORD_000002-2  CUST_00002  16/06/2023   33    Male  Istanbul   
..             ...         ...         ...  ...     ...       ...   
498   ORD_000154-6  CUST_00154  15/10/2023   37  Female     Izmir   
499   ORD_000154-7  CUST_00154  12/12/2023   37  Female     Izmir   
500   ORD_000154-8  CUST_00154  06/02/2024   37  Female     Izmir   
501   ORD_000154-9  CUST_00154  14/02/2024   37  Female     Izmir   
502  ORD_000154-10  CUST_00154  24/02/2024   37  Female     Izmir   

    Product_Category  Unit_Price  Quantity  Discount_Amount  ...  \
0              Books       29.18         1             0.00  ...   
1      Home & Garden      644.40         1           138.05  ...   
2             Sports      332.82         5             0.00  ...   
3               Food       69.30         5            71.05  ...   
4             Beauty      178.15         3             0.00  ...   
..               ...         ...       ...              ...  ...   
498      Electronics     1981.17         5          1289.04  ...   
499      Electronics     5677.63         4          1848.10  ...   
500          Fashion      484.53         1             0.00  ...   
501             Food       56.34         5            47.84  ...   
502             Food       43.26         2             0.00  ...   

     Payment_Method___bank transfer Payment_Method___cash on delivery  \
0                               0.0                               0.0   
1                               0.0                               0.0   
2                               0.0                               0.0   
3                               0.0                               0.0   
4                               0.0                               0.0   
..                              ...                               ...   
498                             0.0                               0.0   
499                             0.0                               0.0   
500                             0.0                               0.0   
501                             0.0                               0.0   
502                             0.0                               0.0   

    Payment_Method___credit card  Payment_Method___debit card  \
0                            0.0                          0.0   
1                            0.0                          0.0   
2                            0.0                          0.0   
3                            0.0                          0.0   
4                            0.0                          0.0   
..                           ...                          ...   
498                          0.0                          0.0   
499                          0.0                          0.0   
500                          0.0                          0.0   
501                          0.0                          0.0   
502                          0.0                          0.0   

     Payment_Method___digital wallet  Device_Type___desktop  \
0                                0.0                    0.0   
1                                0.0                    0.0   
2                                0.0                    0.0   
3                                0.0                    0.0   
4                                0.0                    0.0   
..                               ...                    ...   
498                              0.0                    0.0   
499                              0.0                    0.0   
500                              0.0                    0.0   
501                              0.0                    0.0   
502          

In [14]:
import plotly.express as px
import plotly.graph_objects as go

# base: train 3D
df3 = entrenamiento_pca_objetivo.iloc[:, :3].copy()
df3["objetivo"] = y_train.loc[entrenamiento_pca_objetivo.index].astype(str)

fig3 = px.scatter_3d(
    df3, x="PC1", y="PC2", z="PC3",
    color="objetivo", opacity=0.85,
    title="PC1–PC2–PC3 — Train (objetivo) + Nuevos",
    height=600
)
fig3.update_traces(marker=dict(size=5))

# overlay: nuevos 3D
new3 = T_new_df.loc[:, ["PC1","PC2","PC3"]].copy()
fig3.add_trace(
    go.Scatter3d(
        x=new3["PC1"], y=new3["PC2"], z=new3["PC3"],
        mode="markers",
        name="nuevos",
        marker=dict(size=6, line=dict(width=1)),
        opacity=0.95,
        showlegend=True
    )
)

fig3.update_layout(scene=dict(xaxis_title="PC1", yaxis_title="PC2", zaxis_title="PC3"))
fig3.show()
